## Nationwide Home Values

### Import Libraries

In [59]:
import pandas as pd
import geopandas as gpd
import psycopg2 as psy
import geotable
from kml2geojson import convert
import itertools
import json
from census import Census
from us import states

#### Download Housing Data

In [68]:
homes = pd.read_csv("https://raw.githubusercontent.com/rashida048/Datasets/master/home_data.csv")
homes.to_csv("rawdata.csv")

#### Read in Housing Data

In [61]:
a = pd.read_csv("rawdata.csv", dtype=str)

#### Read in Zip Code Data

Source: https://www.kaggle.com/datasets/danofer/zipcodes-county-fips-crosswalk?resource=download

In [62]:
b = pd.read_csv("data/ZIP-COUNTY-FIPS_2017-06.csv", dtype=str)
b = b.rename({"ZIP":"zip", "STCOUNTYFP":"fips"}, axis='columns')
b

zip         COUNTYNAME STATE   fips CLASSFP
0      36003     Autauga County    AL  01001      H1
1      36006     Autauga County    AL  01001      H1
2      36067     Autauga County    AL  01001      H1
3      36066     Autauga County    AL  01001      H1
4      36703     Autauga County    AL  01001      H1
...      ...                ...   ...    ...     ...
52884  00850   St. Croix Island    VI  78010      H4
52885  00840   St. Croix Island    VI  78010      H4
52886  00820   St. Croix Island    VI  78010      H4
52887  00830    St. John Island    VI  78020      H4
52888  00802  St. Thomas Island    VI  78030      H4

[52889 rows x 5 columns]

---

#### Read in geometry data

---

In [63]:
c = gpd.read_file("data/usacounties.geojson", dtype=str)
c = c.rename({"FIPS":"fips"}, axis='columns')
c


NAME  STATE_NAME STATE_FIPS CNTY_FIPS   fips  \
0         Lake of the Woods   Minnesota         27       077  27077   
1                     Ferry  Washington         53       019  53019   
2                   Stevens  Washington         53       065  53065   
3                  Okanogan  Washington         53       047  53047   
4              Pend Oreille  Washington         53       051  53051   
...                     ...         ...        ...       ...    ...   
3136  Skagway-Hoonah-Angoon      Alaska         02       232  02232   
3137          Yukon-Koyukuk      Alaska         02       290  02290   
3138    Southeast Fairbanks      Alaska         02       240  02240   
3139                 Denali      Alaska         02       068  02068   
3140             Broomfield    Colorado         08       014  08014   

                                               geometry  
0     MULTIPOLYGON (((-95.34283 48.54668, -95.34105 ...  
1     MULTIPOLYGON (((-118.85163 47.94956, -118.8484...  
2     MULTIPOLYGON (((-117.43883 48.04412, -117.5421...  
3     MULTIPOLYGON (((-118.97209 47.93915, -118.9740...  
4     MULTIPOLYGON (((-117.43858 48.99992, -117.0320...  
...                                                 ...  
3136  MULTIPOLYGON (((-137.80952 58.71648, -137.4674...  
3137  MULTIPOLYGON (((-161.04770 62.20469, -160.9942...  
3138  MULTIPOLYGON (((-146.96382 63.46070, -146.9573...  
3139  MULTIPOLYGON (((-152.98947 62.74900, -152.4877...  
3140  MULTIPOLYGON (((-105.05201 39.99761, -104.9913...  

[3141 rows x 6 columns]

---

#### Merge Zip, FIPS, & Geometry 

---

In [65]:
# Group DataFrame A by 'fips' and create a list of zip codes for each group
zip_codes = b.groupby('fips')['zip'].apply(list)

# Merge the zip_codes Series with DataFrame B on 'fips'
c = c.merge(zip_codes, on='fips')

# Rename the new column to 'zip_codes'
c = c.rename(columns={'zip_code': 'zip_codes'})
c

NAME  STATE_NAME STATE_FIPS CNTY_FIPS   fips  \
0       Lake of the Woods   Minnesota         27       077  27077   
1                   Ferry  Washington         53       019  53019   
2                 Stevens  Washington         53       065  53065   
3                Okanogan  Washington         53       047  53047   
4            Pend Oreille  Washington         53       051  53051   
...                   ...         ...        ...       ...    ...   
3131              Yakutat      Alaska         02       282  02282   
3132        Yukon-Koyukuk      Alaska         02       290  02290   
3133  Southeast Fairbanks      Alaska         02       240  02240   
3134               Denali      Alaska         02       068  02068   
3135           Broomfield    Colorado         08       014  08014   

                                               geometry  \
0     MULTIPOLYGON (((-95.34283 48.54668, -95.34105 ...   
1     MULTIPOLYGON (((-118.85163 47.94956, -118.8484...   
2     MULTIPOLYGON (((-117.43883 48.04412, -117.5421...   
3     MULTIPOLYGON (((-118.97209 47.93915, -118.9740...   
4     MULTIPOLYGON (((-117.43858 48.99992, -117.0320...   
...                                                 ...   
3131  MULTIPOLYGON (((-142.19485 60.02709, -142.1832...   
3132  MULTIPOLYGON (((-161.04770 62.20469, -160.9942...   
3133  MULTIPOLYGON (((-146.96382 63.46070, -146.9573...   
3134  MULTIPOLYGON (((-152.98947 62.74900, -152.4877...   
3135  MULTIPOLYGON (((-105.05201 39.99761, -104.9913...   

                                                    zip  
0                   [56686, 56711, 56623, 56741, 56673]  
1     [99138, 99140, 99146, 99107, 99118, 99160, 991...  
2     [99013, 99148, 99026, 99126, 99040, 99006, 991...  
3     [98846, 98829, 99116, 98813, 98833, 98819, 988...  
4     [99139, 99180, 99152, 99006, 99119, 99156, 990...  
...                                                 ...  
3131                                            [99689]  
3132  [99757, 99758, 99733, 99740, 99768, 99724, 996...  
3133  [99764, 99738, 99776, 99731, 99780, 99732, 99737]  
3134                       [99729, 99744, 99743, 99755]  
3135  [80023, 80038, 80516, 80020, 80234, 80603, 800...  

[3136 rows x 7 columns]

### Add in Housing Data 

In [66]:
b_exploded['zip'] = b_exploded['zip'].astype(str)
merged = b_exploded.merge(a, left_on='zip', right_on='zipcode')

In [67]:
merged

NAME  STATE_NAME STATE_FIPS CNTY_FIPS   fips  \
0      Snohomish  Washington         53       061  53061   
1      Snohomish  Washington         53       061  53061   
2      Snohomish  Washington         53       061  53061   
3      Snohomish  Washington         53       061  53061   
4      Snohomish  Washington         53       061  53061   
...          ...         ...        ...       ...    ...   
23831     Pierce  Washington         53       053  53053   
23832     Pierce  Washington         53       053  53053   
23833     Pierce  Washington         53       053  53053   
23834     Pierce  Washington         53       053  53053   
23835     Pierce  Washington         53       053  53053   

                                                geometry    zip Unnamed: 0  \
0      MULTIPOLYGON (((-121.11924 47.77552, -122.3944...  98077        102   
1      MULTIPOLYGON (((-121.11924 47.77552, -122.3944...  98077        108   
2      MULTIPOLYGON (((-121.11924 47.77552, -122.3944...  98077        145   
3      MULTIPOLYGON (((-121.11924 47.77552, -122.3944...  98077        238   
4      MULTIPOLYGON (((-121.11924 47.77552, -122.3944...  98077        270   
...                                                  ...    ...        ...   
23831  MULTIPOLYGON (((-122.80218 47.36074, -122.7995...  98022      20925   
23832  MULTIPOLYGON (((-122.80218 47.36074, -122.7995...  98022      21252   
23833  MULTIPOLYGON (((-122.80218 47.36074, -122.7995...  98022      21256   
23834  MULTIPOLYGON (((-122.80218 47.36074, -122.7995...  98022      21351   
23835  MULTIPOLYGON (((-122.80218 47.36074, -122.7995...  98022      21373   

               id             date  ... grade sqft_above sqft_basement  \
0      7214720075  20141212T000000  ...     8       2190             0   
1      1853000400  20150305T000000  ...    10       3140             0   
2      1526069017  20141203T000000  ...     9       3670             0   
3       326069104  20140701T000000  ...    10       3530           300   
4      4054500390  20141007T000000  ...    11       5310             0   
...           ...              ...  ...   ...        ...           ...   
23831  8141310040  20140627T000000  ...     7       1670             0   
23832  2309710130  20140715T000000  ...     7       1870             0   
23833  8141310080  20141103T000000  ...     7       1670             0   
23834  3421069049  20141021T000000  ...     8       1130             0   
23835  2309710150  20140804T000000  ...     7       2800             0   

      yr_built yr_renovated zipcode      lat      long sqft_living15  \
0         1983            0   98077  47.7731   -122.08          2570   
1         1991            0   98077  47.7304  -122.082          2990   
2         1994            0   98077  47.7421  -122.026          2840   
3         1993            0   98077  47.7641  -122.023          2920   
4         1989            0   98077  47.7285  -122.042          4180   
...        ...          ...     ...      ...       ...           ...   
23831     2014            0   98022  47.1948  -121.975          1670   
23832     2009            0   98022  47.1934  -121.977          2280   
23833     2014            0   98022  47.1948  -121.974          1670   
23834     2006            0   98022  47.2673  -122.027          2092   
23835     2011            0   98022  47.1937  -121.977          2380   

      sqft_lot15  
0          47777  
1          35001  
2          87991  
3         148539  
4          47443  
...          ...  
23831       4622  
23832       5331  
23833       4558  
23834     217800  
23835       5291  

[23836 rows x 29 columns]

In [ ]:
b.explore()

US Census API documentation- https://github.com/datamade/census

In [ ]:
c = Census("5f9687c44873e33b262240225c4ae96dc1f57a56")
c.acs5.get(('NAME', 'B25034_010E'),
          {'for': 'state:{}'.format(states.MD.fips)})

[{'NAME': 'Maryland', 'B25034_010E': 130857.0, 'state': '24'}]

In [ ]:
c.acs1.tables()

[{'name': 'B17015',
  'description': 'POVERTY STATUS IN THE PAST 12 MONTHS OF FAMILIES BY FAMILY TYPE BY SOCIAL SECURITY INCOME BY SUPPLEMENTAL SECURITY INCOME (SSI) AND CASH PUBLIC ASSISTANCE INCOME',
  'variables': 'http://api.census.gov/data/2019/acs/acs1/groups/B17015.json'},
 {'name': 'B18104',
  'description': 'SEX BY AGE BY COGNITIVE DIFFICULTY',
  'variables': 'http://api.census.gov/data/2019/acs/acs1/groups/B18104.json'},
 {'name': 'B17016',
  'description': 'POVERTY STATUS IN THE PAST 12 MONTHS OF FAMILIES BY FAMILY TYPE BY WORK EXPERIENCE OF HOUSEHOLDER AND SPOUSE',
  'variables': 'http://api.census.gov/data/2019/acs/acs1/groups/B17016.json'},
 {'name': 'B18105',
  'description': 'SEX BY AGE BY AMBULATORY DIFFICULTY',
  'variables': 'http://api.census.gov/data/2019/acs/acs1/groups/B18105.json'},
 {'name': 'B17017',
  'description': 'POVERTY STATUS IN THE PAST 12 MONTHS BY HOUSEHOLD TYPE BY AGE OF HOUSEHOLDER',
  'variables': 'http://api.census.gov/data/2019/acs/acs1/groups/B